In [2]:
!pip install "https://github.com/megagonlabs/ginza/releases/download/latest/ginza-latest.tar.gz"

In [2]:
import pkg_resources, imp
imp.reload(pkg_resources)

<module 'pkg_resources' from '/usr/local/lib/python3.7/dist-packages/pkg_resources/__init__.py'>

新しいバージョンがリリースされて、精度向上されている  
https://megagonlabs.github.io/ginza/  
CUDAのバージョン確認  
https://blog.mktia.com/get-cuda-and-cudnn-version/ 

In [8]:
!pip install -U ginza https://github.com/megagonlabs/ginza/releases/download/latest/ja_ginza_electra-latest-with-model.tar.gz

     |████████████████████████████████| 406.0 MB 22 kB/s 
     |████████████████████████████████| 42 kB 1.5 MB/s 
     |████████████████████████████████| 2.6 MB 24.1 MB/s 
     |████████████████████████████████| 998 kB 47.7 MB/s 
     |████████████████████████████████| 636 kB 71.0 MB/s 
     |████████████████████████████████| 895 kB 52.5 MB/s 
     |████████████████████████████████| 3.3 MB 52.9 MB/s 
  Created wheel for ja-ginza-electra: filename=ja_ginza_electra-5.0.0-py3-none-any.whl size=406017806 sha256=4392e3d398965e8356c9157a491957fafa16b0ac01cfc0703e566e4c4011d18a
  Stored in directory: /root/.cache/pip/wheels/24/85/bc/ba8bfdd438033abba357c5f94676b4d3aef4df9951b8a5024c
  Created wheel for ginza: filename=ginza-5.0.2-py3-none-any.whl size=17857 sha256=2684d032cd688a02c3f069bb88a730c9cc0a9e9406aa98ea83a5b2394189803b
  Stored in directory: /root/.cache/pip/wheels/63/3d/ef/46ca55e86d264ddffc04422b20a53d1a0fbd781f1904e2c577
  Created wheel for ginza-transformers: filename=ginza_trans

In [9]:
!cat /usr/local/cuda/version.txt

CUDA Version 11.0.228


In [10]:
!pip install -U "spacy[cuda110]"

     |████████████████████████████████| 75.3 MB 67 kB/s 


https://www.nogawanogawa.com/entry/ginza  
https://www.mojirca.com/2019/10/colab-load-ginza.html  
ランタイムの再起動はやはり必要そう  

In [1]:
import spacy
from spacy import displacy
# GiNZAモデルの読み込み
nlp = spacy.load('ja_ginza_electra')

In [2]:
# googleドライブをマウント
from google.colab import drive 
drive.mount('/content/drive')
# 表示されるリンクをクリックして、アクセスを許可して、最後に表示される文字列を以下の入力欄に入れる

Mounted at /content/drive


In [3]:
# 作業フォルダに移動
%cd '/content/drive/My Drive/work/'

/content/drive/My Drive/work


In [ ]:
import json

input_file = "output_0001.json"
path_w = 'train_0001.txt'

count_length = 0

with open(path_w, mode='w') as f_out:
  with open(input_file) as f_in:
    json_text = json.load(f_in)
    for v_result in json_text.values():
      for v_alternatives in v_result:
        for val_list in v_alternatives.values():
          if isinstance(val_list, list):
            for val in val_list:
              count_length += len(val.get('transcript'))
              f_out.write(val.get('transcript'))
              f_out.write('。\n')

print('文字数')
print(count_length)

4171


In [4]:
filepath = "train_all.txt"
with open(filepath) as f:
    s = f.read()

# 文章全体を解析
doc = nlp(s) 

In [5]:
#抽出したエンティティの種類に対して色を指定する
colors = {"COUNTRY":"#00cc00", "CITY":"#00cc00", "GPE_OTHER":"#00cc00","OCCASION_OTHER":"#00cc00",
          "LOCATION":"#00cc00", "LOCATION_OTHER":"#00cc00","DOMESTIC_REGION":"#00cc00","PROVINCE":"#00cc00",
          "STATION":"#00cc00", "CONTINENTAL_REGION":"#00cc00","THEATER":"#00cc00",

          "TIME":"#adff2f","DATE":"#adff2f","DAY_OF_WEEK":"#adff2f",
          "PERIOD_YEAR":"#adff2f", "PERIOD_MONTH":"#adff2f", "PERIOD_DAY":"#adff2f",

          "FLORA":"#adff99","FLORA_PART":"#adff99",
          "DISH":"#ffeb99","FOOD_OTHER":"#ffeb99",

          "AGE":"#3385ff","N_PERSON":"#3385ff","N_EVENT":"#3385ff","N_LOCATION_OTHER":"#3385ff","RANK":"#3385ff",
          "N_PRODUCT":"#3385ff","":"#3385ff","":"#3385ff","":"#3385ff","MEASUREMENT_OTHER":"#3385ff","PERCENT":"#3385ff",
          "N_ORGANIZATION":"#3385ff", "ORDINAL_NUMBER":"#3385ff", "N_FACILITY":"#3385ff","SPEED":"#3385ff",
          "PHONE_NUMBER":"#3385ff",

          "MONEY":"#ffff00",

          "COMPANY":"#99c2ff", "SCHOOL":"#99c2ff", "INTERNATIONAL_ORGANIZATION":"#99c2ff",
          "GOE_OTHER":"#99c2ff", "SHOW_ORGANIZATION":"#99c2ff","CORPORATION_OTHER":"#99c2ff",

          "CLOTHING":"#ff66a3",
          "PRODUCT_OTHER":"#ff66a3",

          "PERSON":"#c266ff",
          "POSITION_VOCATION":"#ebccff",

          "MUSIC":"#ff7f50", "MOVIE":"#ff7f50", "GAME":"#ff7f50", "SPORT":"#ff7f50", "BOOK":"#ff7f50", 
          "BROADCAST_PROGRAM":"#ff7f50", 

          "ANIMAL_DISEASE":"#cd5c5c"
          }

options = {"colors": colors}
displacy.render(doc, style="ent", options=options, jupyter=True)

In [6]:
result_text = ''
# 文単位でループ
for sent in doc.sents:
  # 形態素単位でループ
  for token in sent:
    hasText = True
    # 固有表現の取得
    for ent in sent.ents:
      # 置換しない固有表現
      if ent.label_ in ['LOC', 'DATE', 'TIME', 'PERCENT']:
        continue
      # 固有表現のテキストが一致した場合置換
      if token.text == ent.text:
        hasText = False
        # ent.label_ の意味合い
        # 組織名 (ORGANIZATION)、人名 (PERSON)、地名 (LOCATION)、日付表現 (DATE)、時間表現 (TIME)、金額表現 (MONEY)、割合表現 (PERCENT)
        result_text = result_text + ent.label_
        # 一度一致したら次の形態素の解析に移る
        break
    if hasText:
      # 固有表現がないのでそのまま保持
      result_text = result_text + token.text
  # 文章単位で改行
  result_text = result_text + '\n'

In [8]:
result_text

'2021年Gameでは初めての試合ということになります\n\n主催の興行ということになります\n\n今日は西日本全国各地で雨が降っています。\n\nDateの嵐となっています。\n暖かい日が続いたり、時に冷たい雨が降ったり、まさにGame、Dateの訪れを感じさせるような季節となっています。\n\nNature_Colorコーナーから入場してきました\nShow_Organization、これまで6戦戦って2勝4敗\n\nこれが7戦目ということになります。\nデビューしてからなかなか勝てずに、3連敗からの2連勝もあり、\n昨年の10月に敗れて、再び、これが再戦ということになります。\n\n強い気持ちを持ってどんどん前に出る、Pro_Sports_OrganizationのSport、今日も見られるんでしょうか。\n\n階段の前で、精神統一、リングを見ました。\n\n階段を踏みしめるように上がって、今リングインです。\n\nShow_Organization、Nature_Colorコーナーから入場しました。\n\n\n女子フライ級4回戦で行われる、RAIAN対PERSONの一戦。\n\n敗れた後、２連勝もあって、ピンチの中でもしっかり、気持ちで負けないメンタルを培ってきましたと、いう風に語っていました\n\nそしてNature_Colorコーナーから入場してきましたPERSON。\n\n\n\n日本女子フライ級5位にランクインしているPERSON、入場してきました。\n\n水を含み、階段を上っていきます。\n\nこれが4戦目\n\nこれまでデビューしてから負けを知りません。\nPERSON、今リングインです。\n\n地元の観客からは、大きな拍手が送られています。\nPERSON\nこれが4戦目。\n\n地元での試合ということになります。\n\n観客に向かって礼をして試合に臨みます。\n\nN_Personにとってこれが分岐点となる試合となります。\n\n女子フライ級4回戦で行われます。\n\nRAIAN対PERSONの一戦、N_Personにとってさらに上のランクに上がるためには、勝たなければいけない試合ということになります。\n\n気合いは十分。\n\n女子フライ級4回戦\n。\n\nRAIAN対PERSONの一戦です\n\nまず左のジャブを打って行ったのはPr

In [7]:
path_w = 'train_all_ent.txt'
with open(path_w, mode='w') as f_out:
  f_out.write(result_text)